In [71]:
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from pytorch_tabnet.tab_model import TabNetClassifier
#from pytorch_tabnet.tab_model import TabNetModel
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
import statsmodels.api as sm
import warnings
import shap
import optuna
import torch
from sklearn import svm
import tensorflow as tf
from tensorflow import feature_column
from tensorflow.keras import layers
from tqdm.auto import tqdm
from pytorch_tabnet.tab_model import TabNetRegressor
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_validate
from sklearn.ensemble import VotingClassifier
from sklearn.ensemble import VotingRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import StratifiedKFold
from pycaret.regression import *
from xgboost import XGBRegressor
from xgboost import XGBClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.tree import ExtraTreeRegressor
from sklearn.experimental import enable_iterative_imputer 
from sklearn.impute import KNNImputer
from sklearn.impute import IterativeImputer
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, Pool
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import AdaBoostRegressor
from catboost import CatBoostRegressor
from catboost import CatBoostClassifier
from sklearn.metrics import mean_squared_error
from sklearn.impute import KNNImputer
from sklearn.decomposition import PCA

In [72]:
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', None)

In [73]:
train_data = pd.read_csv("./train.csv")

In [74]:
train_data.describe()

Y_Class   Y_Quality         X_1         X_2    X_3    X_4  \
count  598.000000  598.000000  349.000000  349.000000  349.0  349.0   
mean     1.025084    0.530896    2.409742   95.123209    0.0   45.0   
std      0.565069    0.007401    5.895256    4.107640    0.0    0.0   
min      0.000000    0.500856    1.000000   87.000000    0.0   45.0   
25%      1.000000    0.527535    2.000000   93.000000    0.0   45.0   
50%      1.000000    0.530436    2.000000   95.000000    0.0   45.0   
75%      1.000000    0.533433    2.000000   98.000000    0.0   45.0   
max      2.000000    0.578841  103.000000  102.000000    0.0   45.0   

              X_5    X_6         X_7         X_8         X_9   X_10  \
count  349.000000  349.0  349.000000  349.000000  349.000000  349.0   
mean    10.392550    0.0   48.802292   10.048711   41.469914    2.0   
std      0.489019    0.0    4.373824    0.215571   10.515032    0.0   
min     10.000000    0.0   45.000000   10.000000   31.000000    2.0   
25%     10.000000    0.0   45.000000   10.000000   31.000000    2.0   
50%     10.000000    0.0   45.000000   10.000000   31.000000    2.0   
75%     11.000000    0.0   51.000000   10.000000   52.000000    2.0   
max     11.000000    0.0   62.000000   11.000000   52.000000    2.0   

             X_11        X_12        X_13   X_14        X_15        X_16  \
count  349.000000  349.000000  349.000000  349.0  349.000000  349.000000   
mean   497.050716  503.401433  488.307736    0.0    0.005731  247.542120   
std     17.264680   17.975169   17.335538    0.0    0.107058    0.052271   
min    433.900000  440.200000  424.300000    0.0    0.000000  247.400000   
25%    487.400000  493.400000  478.500000    0.0    0.000000  247.500000   
50%    499.900000  505.000000  489.800000    0.0    0.000000  247.500000   
75%    509.600000  516.300000  500.900000    0.0    0.000000  247.600000   
max    527.200000  538.000000  518.700000    0.0    2.000000  247.700000   

             X_17        X_18   X_19        X_20        X_21        X_22  \
count  349.000000  349.000000  349.0  349.000000  349.000000  349.000000   
mean   248.068195  247.311748  250.0  497.982808  507.375358  492.303725   
std      0.111636    0.076222    0.0   17.745316   18.512331   18.048610   
min    247.700000  247.100000  250.0  469.000000  478.000000  461.000000   
25%    248.000000  247.300000  250.0  485.000000  494.000000  479.000000   
50%    248.100000  247.300000  250.0  495.000000  505.000000  490.000000   
75%    248.100000  247.400000  250.0  507.000000  517.000000  501.000000   
max    248.400000  247.500000  250.0  569.000000  583.000000  562.000000   

               X_23        X_24          X_25   X_26   X_27   X_28   X_29  \
count  3.490000e+02  349.000000  3.490000e+02  349.0  349.0  349.0  349.0   
mean   1.900000e-01    0.191347  1.900000e-01  155.0  155.0  155.0  155.0   
std    8.894536e-16    0.003419  8.894536e-16    0.0    0.0    0.0    0.0   
min    1.900000e-01    0.190000  1.900000e-01  155.0  155.0  155.0  155.0   
25%    1.900000e-01    0.190000  1.900000e-01  155.0  155.0  155.0  155.0   
50%    1.900000e-01    0.190000  1.900000e-01  155.0  155.0  155.0  155.0   
75%    1.900000e-01    0.190000  1.900000e-01  155.0  155.0  155.0  155.0   
max    1.900000e-01    0.200000  1.900000e-01  155.0  155.0  155.0  155.0   

        X_30   X_31   X_32   X_33   X_34   X_35   X_36   X_37        X_38  \
count  349.0  349.0  349.0  349.0  349.0  349.0  349.0  349.0  349.000000   
mean   185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0    0.077364   
std      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.001698   
min    185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0    0.075000   
25%    185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0    0.076000   
50%    185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0    0.078000   
75%    185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0    0.079000   
max    185.0  185.0  185.0  185.0  155.0  155.0  1

In [75]:
train_data['YEAR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.year
train_data['MONTH'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.month
train_data['DAY'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day
train_data['HOUR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.hour
train_data['MINUTE'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.minute
train_data['DAY_OF_WEEK'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day_name()

train_data = train_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE', 'HOUR'], axis = 1)

In [76]:
colls = []
for coll in train_data :
    if 'X' in coll and train_data[coll].isna().sum() == 598 :
        colls.append(coll)
print(len(colls))

train_data.drop(colls, inplace = True, axis = 1)

82


In [77]:
train_data.loc[train_data.LINE == 'T050304','LINE'] = 1
train_data.loc[train_data.LINE == 'T050307','LINE'] = 2
train_data.loc[train_data.LINE == 'T010305','LINE'] = 3
train_data.loc[train_data.LINE == 'T010306','LINE'] = 4
train_data.loc[train_data.LINE == 'T100304','LINE'] = 5
train_data.loc[train_data.LINE == 'T100306','LINE'] = 6

train_data.loc[train_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
train_data.loc[train_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
train_data.loc[train_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
train_data.loc[train_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
train_data.loc[train_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
train_data.loc[train_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
train_data.loc[train_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

train_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
train_data

Y_Class  Y_Quality LINE PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  X_6  \
0          1   0.533433    1         A_31   NaN   NaN  NaN   NaN   NaN  NaN   
1          2   0.541819    2         A_31   NaN   NaN  NaN   NaN   NaN  NaN   
2          1   0.531267    1         A_31   NaN   NaN  NaN   NaN   NaN  NaN   
3          2   0.537325    2         A_31   NaN   NaN  NaN   NaN   NaN  NaN   
4          1   0.531590    1         A_31   NaN   NaN  NaN   NaN   NaN  NaN   
..       ...        ...  ...          ...   ...   ...  ...   ...   ...  ...   
593        1   0.526546    6         T_31   2.0  95.0  0.0  45.0  10.0  0.0   
594        0   0.524022    1         A_31   NaN   NaN  NaN   NaN   NaN  NaN   
595        0   0.521289    1         A_31   NaN   NaN  NaN   NaN   NaN  NaN   
596        1   0.531375    5         O_31  40.0  94.0  0.0  45.0  11.0  0.0   
597        1   0.533702    6         O_31  21.0  87.0  0.0  45.0  10.0  0.0   

      X_7   X_8   X_9  X_10   X_11   X_12   X_13  X_14  X_15   X_16   X_17  \
0     NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN   
1     NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN   
2     NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN   
3     NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN   
4     NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN   
..    ...   ...   ...   ...    ...    ...    ...   ...   ...    ...    ...   
593  50.0  10.0  52.0   2.0  468.9  473.9  459.2   0.0   0.0  247.5  248.0   
594   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN   
595   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN   
596  45.0  10.0  31.0   2.0  505.8  510.9  497.1   0.0   0.0  247.5  248.1   
597  61.0  10.0  52.0   2.0  470.6  474.9  462.9   0.0   0.0  247.5  248.0   

      X_18   X_19   X_20   X_21   X_22  X_23  X_24  X_25   X_26   X_27   X_28  \
0      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN   
..     ...    ...    ...    ...    ...   ...   ...   ...    ...    ...    ...   
593  247.3  250.0  527.0  538.0  522.0  0.19  0.19  0.19  155.0  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN   
596  247.3  250.0  489.0  498.0  485.0  0.19  0.19  0.19  155.0  155.0  155.0   
597  247.3  250.0  525.0  534.0  520.0  0.19  0.20  0.19  155.0  155.0  155.0   

      X_29   X_30   X_31   X_32   X_33   X_34   X_35   X_36   X_37   X_38  \
0      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
593  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0  0.075   
594    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
596  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0  0.078   
597  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0  0.077   

     X_39  X_40  X_41  X_42  X_43  X_44  X_45  X_46  X_47  X_48  X_49  X_50  \
0     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN

In [78]:
A_31 = train_data[train_data['PRODUCT_CODE'] == 'A_31']
T_31 = train_data[train_data['PRODUCT_CODE'] == 'T_31']
O_31 = train_data[train_data['PRODUCT_CODE'] == 'O_31']

A_31.drop(['PRODUCT_CODE'], axis = 1, inplace = True)
T_31.drop(['PRODUCT_CODE'], axis = 1, inplace = True)
O_31.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [79]:
A_31_col = []
for col in A_31 :
    if 'X' in col and A_31[col].isna().sum() == len(A_31) :
        A_31_col.append(col)
print(len(A_31_col))

T_31_col = []
for col in T_31 :
    if 'X' in col and T_31[col].isna().sum() == len(T_31) :
        T_31_col.append(col)
print(len(T_31_col))

O_31_col = []
for col in O_31 :
    if 'X' in col and O_31[col].isna().sum() == len(O_31) :
        O_31_col.append(col)
print(len(O_31_col))

677
2116
2126


In [80]:
A_31.describe()

Y_Class   Y_Quality  X_1  X_2  X_3  X_4  X_5  X_6  X_7  X_8  X_9  \
count  249.000000  249.000000  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
mean     1.044177    0.531697  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
std      0.725442    0.009965  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
min      0.000000    0.500856  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
25%      1.000000    0.525221  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
50%      1.000000    0.530606  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
75%      2.000000    0.536206  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
max      2.000000    0.578841  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   

       X_10  X_11  X_12  X_13  X_14  X_15  X_16  X_17  X_18  X_19  X_20  X_21  \
count   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
mean    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
std     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
min     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
25%     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
50%     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
75%     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
max     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   

       X_22  X_23  X_24  X_25  X_26  X_27  X_28  X_29  X_30  X_31  X_32  X_33  \
count   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
mean    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
std     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
min     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
25%     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
50%     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
75%     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
max     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   

       X_34  X_35  X_36  X_37  X_38  X_39  X_40  X_41  X_42  X_43  X_44  X_45  \
count   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
mean    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
std     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
min     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
25%     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
50%     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
75%     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
max     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   

       X_46  X_47  X_48  X_49  X_50  X_51  X_52  X_53  X_54  X_55  X_56  X_57  \
count   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
mean    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
std     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
min     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
25%     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
50%     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
75%     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
max     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   

       X_58  X_59  X_60  X_61  X_62  X_63  X_64  X_65  X_66  X_67  X_68  X_69  \
count   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
mean    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
std     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
min     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   N

In [81]:
A_31.drop(A_31_col, inplace = True, axis = 1)
T_31.drop(T_31_col, inplace = True, axis = 1)
O_31.drop(O_31_col, inplace = True, axis = 1)

#A_31 = A_31.fillna(A_31.mean())
#T_31 = T_31.fillna(T_31.mean())
#O_31 = O_31.fillna(O_31.mean())

A_31 = A_31.fillna(0)
T_31 = T_31.fillna(0)
O_31 = O_31.fillna(0)

In [82]:
A_31_cols = []
for col in A_31 :
    if 'X' in col and A_31[col].std() == 0 :
        A_31_cols.append(col)
print(len(A_31_cols))

T_31_cols = []
for col in T_31 :
    if 'X' in col and T_31[col].std() == 0 :
        T_31_cols.append(col)
print(len(T_31_cols))

O_31_cols = []
for col in O_31 :
    if 'X' in col and O_31[col].std() == 0 :
        O_31_cols.append(col)
print(len(O_31_cols))

145
92
153


In [83]:
A_31.drop(A_31_cols, inplace = True, axis = 1)
T_31.drop(T_31_cols, inplace = True, axis = 1)
O_31.drop(O_31_cols, inplace = True, axis = 1)

In [84]:
T05 = A_31
T01 = T_31
T10 = pd.concat([O_31, O_31, O_31, O_31]).reset_index()

In [85]:
T05_75 = []
for x in T05 :
    if T05[x].quantile(q = 0.75) == 0 :
        T05_75.append(x)

T01_75 = []
for x in T01 :
    if T01[x].quantile(q = 0.75) == 0 :
        T01_75.append(x)
        
T10_75 = []
for x in T10 :
    if T10[x].quantile(q = 0.75) == 0 :
        T10_75.append(x)

In [86]:
T05.drop(T05_75, inplace = True, axis = 1)
T01.drop(T01_75, inplace = True, axis = 1)
T10.drop(T10_75, inplace = True, axis = 1)

# A_31

In [88]:
T05_class = T05['Y_Class']
T05_target = T05['Y_Quality']
T05_data = T05.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [89]:
T_05c = T05_data.columns
T_05scaler = RobustScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)

T05_y_class = pd.DataFrame(T05_target, columns = ['Y_Quality'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_data = pd.concat([T05_data, T05_y_class], axis = 1)
T05_data = T05_data.set_index('index')
T05_data.drop(['Y_Quality'], axis = 1, inplace = True)
T05_data

LINE     X_128     X_129  X_132     X_133  X_134  X_135     X_136  \
index                                                                          
0     -0.666667  0.999488  0.999105   0.95  0.952381   0.95    1.0  0.901186   
1     -0.333333  0.000000  0.000000   1.00  1.000000   1.00    1.0  1.632411   
2     -0.666667  0.999744  0.999361   0.95  0.952381   0.95    1.0  0.901186   
3     -0.333333  0.000000  0.000000   1.00  1.000000   1.00    1.0  1.636364   
4     -0.666667  1.000000  0.999616   0.95  0.952381   0.90    1.0  0.901186   
...         ...       ...       ...    ...       ...    ...    ...       ...   
583   -0.666667  1.524882  1.524297   0.95  0.952381   0.95    1.0  0.909091   
584    0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
585    0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
594   -0.666667  1.894589  1.893862   0.95  0.952381   0.95    1.0  1.201581   
595   -0.666667  1.894972  1.894246   0.95  0.952381   0.95    1.0  1.201581   

          X_137  X_138     X_139     X_140     X_141    X_144  X_145  \
index                                                                  
0      0.901186  0.900  0.999486  0.998809  1.002474  1.00000    1.0   
1      1.636364  1.656  1.010460  1.013610  1.017671  1.00004    1.0   
2      0.901186  0.900  1.001029  0.999660  1.012370  1.00004    1.0   
3      1.636364  1.656  1.011317  1.014120  0.993462  1.00004    1.0   
4      0.901186  0.900  1.000000  0.999149  1.000000  1.00000    1.0   
...         ...    ...       ...       ...       ...      ...    ...   
583    0.909091  0.920  1.000514  1.000851  0.982329  1.00004    1.0   
584    0.000000  0.000  0.000000  0.000000  0.000000  0.00000    0.0   
585    0.000000  0.000  0.000000  0.000000  0.000000  0.00000    0.0   
594    1.201581  1.216  1.009774  1.011569  1.015727  1.00004    1.0   
595    1.201581  1.216  1.009602  1.011569  1.008659  1.00000    1.0   

          X_146  X_147     X_148     X_149     X_150     X_151  X_152  \
index                                                                   
0      1.000809    1.0  1.000000  1.002304  1.002353  0.999444    1.0   
1      1.008776    1.0  0.988318  0.997696  0.985882  0.999444    1.0   
2      1.007442    1.0  0.997664  1.000000  1.000000  0.999444    1.0   
3      0.983823    1.0  0.988318  0.997696  0.985882  0.999444    1.0   
4      0.996765    1.0  1.000000  1.000000  1.002353  1.000000    1.0   
...         ...    ...       ...       ...       ...       ...    ...   
583    0.973510    1.0  1.000000  1.002304  1.000000  1.000000    1.0   
584    0.000000    0.0  0.000000  0.000000  0.000000  0.000000    0.0   
585    0.000000    0.0  0.000000  0.000000  0.000000  0.000000    0.0   
594    1.002143    1.0  0.990654  0.993088  0.988235  0.999444    1.0   
595    0.993327    1.0  0.990654  0.993088  0.988235  1.000000    1.0   

          X_153  X_154     X_155     X_156     X_157  X_158     X_159  X_160  \
index                                                                          
0      1.000000    1.0  1.000000  1.000000  1.000000    1.0  0.999535    1.0   
1      0.999444    1.0  0.999535  1.000465  0.999535    1.0  0.999535    1.0   
2      0.999444    1.0  1.000000  1.000000  1.000000    1.0  1.000000    1.0   
3      1.000000    1.0  1.000000  1.000000  1.000000    1.0  1.000000    1.0   
4      0.999444    1.0  1.000000  1.000465  1.000465    1.0  0.999535    1.0   
...         ...    ...       ...       ...       ...    ...       ...    ...   
583    1.000000    1.0  0.999535  1.000000  1.000000    1.0  0.999535    1.0   
584    0.000000    0.0  0.000000  0.000000  0.000000    0.0  0.000000    0.0   
585    0.000000    0.0  0.000000  0.000000  0.000000    0.0  0.000000    0.0   
594    1.000000    1.0  1.000000  1.000000  1.000000    1.0  0.999535    1.0   
595    1.000000    1.0  1.000000  1.000465  1.000465    1.0  0.999535    1.0   

       X_161  X_162     X_163     X_164   

In [90]:
#13
setup_rgs = setup(data = T05_data, target = T05_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [91]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbr = create_model('gbr', fold = 5)
T05_total_models.append(T05_model_gbr)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [92]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbr = tune_model(T05_model_gbr, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [93]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbr, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]

for model in T05_tuned_models:
    display(predict_model(model))

LINE     X_128     X_129  X_132     X_133  X_134  X_135     X_136  \
174  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
175  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
176  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
177 -0.666667  1.000384  1.000000   0.95  0.952381   0.95    1.0  0.901186   
178 -0.333333  0.000000  0.000000   1.00  1.000000   0.95    1.0  2.553360   
..        ...       ...       ...    ...       ...    ...    ...       ...   
244  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
245  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
246 -0.666667  1.524882  1.524297   0.95  0.952381   0.95    1.0  0.909091   
247  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
248  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   

        X_137  X_138  ...    X_2865    X_2866    X_2867    X_2868    X_2869  \
174  0.000000  0.000  ...  0.000000  0.000000  0.000000  0.000000  0.000000   
175  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
176  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
177  0.901186  0.900  ... -0.746479  0.620347  0.768603  0.769817  0.559528   
178  2.553360  2.584  ... -0.746479  1.016797  1.039339  1.193458  1.068784   
..        ...    ...  ...       ...       ...       ...       ...       ...   
244  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
245  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
246  0.909091  0.920  ... -0.746479  0.987020  1.106699  1.095926  1.035390   
247  0.000000  0.000  ...  0.267606  0.000000  0.000000  0.000000  0.000000   
248  0.000000  0.000  ...  0.084507  0.000000  0.000000  0.000000  0.000000   

       X_2870  X_2871  DAY_OF_WEEK  Y_Quality  prediction_label  
174  0.000000     0.0        -0.50   0.528270          0.536436  
175  0.000000     0.0        -0.75   0.534716          0.538135  
176  0.000000     0.0         0.00   0.545925          0.543055  
177  1.193453     0.0        -1.00   0.533665          0.535079  
178  1.012566     1.0        -0.50   0.542848          0.546591  
..        ...     ...          ...        ...               ...  
244  0.000000     0.0         0.00   0.533051          0.533037  
245  0.000000     0.0        -0.75   0.534065          0.537437  
246  0.980143     1.0        -1.00   0.522340          0.524427  
247  0.000000     0.0         0.00   0.533079          0.535474  
248  0.000000     0.0         0.00   0.544089          0.537671  

[75 rows x 1394 columns]

LINE     X_128     X_129  X_132     X_133  X_134  X_135     X_136  \
174  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
175  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
176  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
177 -0.666667  1.000384  1.000000   0.95  0.952381   0.95    1.0  0.901186   
178 -0.333333  0.000000  0.000000   1.00  1.000000   0.95    1.0  2.553360   
..        ...       ...       ...    ...       ...    ...    ...       ...   
244  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
245  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
246 -0.666667  1.524882  1.524297   0.95  0.952381   0.95    1.0  0.909091   
247  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
248  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   

        X_137  X_138  ...    X_2865    X_2866    X_2867    X_2868    X_2869  \
174  0.000000  0.000  ...  0.000000  0.000000  0.000000  0.000000  0.000000   
175  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
176  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
177  0.901186  0.900  ... -0.746479  0.620347  0.768603  0.769817  0.559528   
178  2.553360  2.584  ... -0.746479  1.016797  1.039339  1.193458  1.068784   
..        ...    ...  ...       ...       ...       ...       ...       ...   
244  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
245  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
246  0.909091  0.920  ... -0.746479  0.987020  1.106699  1.095926  1.035390   
247  0.000000  0.000  ...  0.267606  0.000000  0.000000  0.000000  0.000000   
248  0.000000  0.000  ...  0.084507  0.000000  0.000000  0.000000  0.000000   

       X_2870  X_2871  DAY_OF_WEEK  Y_Quality  prediction_label  
174  0.000000     0.0        -0.50   0.528270          0.532153  
175  0.000000     0.0        -0.75   0.534716          0.533981  
176  0.000000     0.0         0.00   0.545925          0.544670  
177  1.193453     0.0        -1.00   0.533665          0.533228  
178  1.012566     1.0        -0.50   0.542848          0.547030  
..        ...     ...          ...        ...               ...  
244  0.000000     0.0         0.00   0.533051          0.534634  
245  0.000000     0.0        -0.75   0.534065          0.535080  
246  0.980143     1.0        -1.00   0.522340          0.527315  
247  0.000000     0.0         0.00   0.533079          0.534953  
248  0.000000     0.0         0.00   0.544089          0.539931  

[75 rows x 1394 columns]

LINE     X_128     X_129  X_132     X_133  X_134  X_135     X_136  \
174  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
175  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
176  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
177 -0.666667  1.000384  1.000000   0.95  0.952381   0.95    1.0  0.901186   
178 -0.333333  0.000000  0.000000   1.00  1.000000   0.95    1.0  2.553360   
..        ...       ...       ...    ...       ...    ...    ...       ...   
244  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
245  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
246 -0.666667  1.524882  1.524297   0.95  0.952381   0.95    1.0  0.909091   
247  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
248  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   

        X_137  X_138  ...    X_2865    X_2866    X_2867    X_2868    X_2869  \
174  0.000000  0.000  ...  0.000000  0.000000  0.000000  0.000000  0.000000   
175  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
176  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
177  0.901186  0.900  ... -0.746479  0.620347  0.768603  0.769817  0.559528   
178  2.553360  2.584  ... -0.746479  1.016797  1.039339  1.193458  1.068784   
..        ...    ...  ...       ...       ...       ...       ...       ...   
244  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
245  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
246  0.909091  0.920  ... -0.746479  0.987020  1.106699  1.095926  1.035390   
247  0.000000  0.000  ...  0.267606  0.000000  0.000000  0.000000  0.000000   
248  0.000000  0.000  ...  0.084507  0.000000  0.000000  0.000000  0.000000   

       X_2870  X_2871  DAY_OF_WEEK  Y_Quality  prediction_label  
174  0.000000     0.0        -0.50   0.528270          0.529563  
175  0.000000     0.0        -0.75   0.534716          0.533038  
176  0.000000     0.0         0.00   0.545925          0.544604  
177  1.193453     0.0        -1.00   0.533665          0.533249  
178  1.012566     1.0        -0.50   0.542848          0.549060  
..        ...     ...          ...        ...               ...  
244  0.000000     0.0         0.00   0.533051          0.534131  
245  0.000000     0.0        -0.75   0.534065          0.533817  
246  0.980143     1.0        -1.00   0.522340          0.524607  
247  0.000000     0.0         0.00   0.533079          0.535199  
248  0.000000     0.0         0.00   0.544089          0.539732  

[75 rows x 1394 columns]

LINE     X_128     X_129  X_132     X_133  X_134  X_135     X_136  \
174  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
175  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
176  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
177 -0.666667  1.000384  1.000000   0.95  0.952381   0.95    1.0  0.901186   
178 -0.333333  0.000000  0.000000   1.00  1.000000   0.95    1.0  2.553360   
..        ...       ...       ...    ...       ...    ...    ...       ...   
244  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
245  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
246 -0.666667  1.524882  1.524297   0.95  0.952381   0.95    1.0  0.909091   
247  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
248  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   

        X_137  X_138  ...    X_2865    X_2866    X_2867    X_2868    X_2869  \
174  0.000000  0.000  ...  0.000000  0.000000  0.000000  0.000000  0.000000   
175  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
176  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
177  0.901186  0.900  ... -0.746479  0.620347  0.768603  0.769817  0.559528   
178  2.553360  2.584  ... -0.746479  1.016797  1.039339  1.193458  1.068784   
..        ...    ...  ...       ...       ...       ...       ...       ...   
244  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
245  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
246  0.909091  0.920  ... -0.746479  0.987020  1.106699  1.095926  1.035390   
247  0.000000  0.000  ...  0.267606  0.000000  0.000000  0.000000  0.000000   
248  0.000000  0.000  ...  0.084507  0.000000  0.000000  0.000000  0.000000   

       X_2870  X_2871  DAY_OF_WEEK  Y_Quality  prediction_label  
174  0.000000     0.0        -0.50   0.528270          0.529879  
175  0.000000     0.0        -0.75   0.534716          0.541258  
176  0.000000     0.0         0.00   0.545925          0.548352  
177  1.193453     0.0        -1.00   0.533665          0.531918  
178  1.012566     1.0        -0.50   0.542848          0.547366  
..        ...     ...          ...        ...               ...  
244  0.000000     0.0         0.00   0.533051          0.533062  
245  0.000000     0.0        -0.75   0.534065          0.535895  
246  0.980143     1.0        -1.00   0.522340          0.527354  
247  0.000000     0.0         0.00   0.533079          0.540333  
248  0.000000     0.0         0.00   0.544089          0.541609  

[75 rows x 1394 columns]

LINE     X_128     X_129  X_132     X_133  X_134  X_135     X_136  \
174  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
175  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
176  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
177 -0.666667  1.000384  1.000000   0.95  0.952381   0.95    1.0  0.901186   
178 -0.333333  0.000000  0.000000   1.00  1.000000   0.95    1.0  2.553360   
..        ...       ...       ...    ...       ...    ...    ...       ...   
244  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
245  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
246 -0.666667  1.524882  1.524297   0.95  0.952381   0.95    1.0  0.909091   
247  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
248  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   

        X_137  X_138  ...    X_2865    X_2866    X_2867    X_2868    X_2869  \
174  0.000000  0.000  ...  0.000000  0.000000  0.000000  0.000000  0.000000   
175  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
176  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
177  0.901186  0.900  ... -0.746479  0.620347  0.768603  0.769817  0.559528   
178  2.553360  2.584  ... -0.746479  1.016797  1.039339  1.193458  1.068784   
..        ...    ...  ...       ...       ...       ...       ...       ...   
244  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
245  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
246  0.909091  0.920  ... -0.746479  0.987020  1.106699  1.095926  1.035390   
247  0.000000  0.000  ...  0.267606  0.000000  0.000000  0.000000  0.000000   
248  0.000000  0.000  ...  0.084507  0.000000  0.000000  0.000000  0.000000   

       X_2870  X_2871  DAY_OF_WEEK  Y_Quality  prediction_label  
174  0.000000     0.0        -0.50   0.528270          0.531722  
175  0.000000     0.0        -0.75   0.534716          0.535877  
176  0.000000     0.0         0.00   0.545925          0.547084  
177  1.193453     0.0        -1.00   0.533665          0.534013  
178  1.012566     1.0        -0.50   0.542848          0.549152  
..        ...     ...          ...        ...               ...  
244  0.000000     0.0         0.00   0.533051          0.535305  
245  0.000000     0.0        -0.75   0.534065          0.532752  
246  0.980143     1.0        -1.00   0.522340          0.524022  
247  0.000000     0.0         0.00   0.533079          0.537063  
248  0.000000     0.0         0.00   0.544089          0.540165  

[75 rows x 1394 columns]

LINE     X_128     X_129  X_132     X_133  X_134  X_135     X_136  \
174  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
175  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
176  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
177 -0.666667  1.000384  1.000000   0.95  0.952381   0.95    1.0  0.901186   
178 -0.333333  0.000000  0.000000   1.00  1.000000   0.95    1.0  2.553360   
..        ...       ...       ...    ...       ...    ...    ...       ...   
244  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
245  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
246 -0.666667  1.524882  1.524297   0.95  0.952381   0.95    1.0  0.909091   
247  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
248  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   

        X_137  X_138  ...    X_2865    X_2866    X_2867    X_2868    X_2869  \
174  0.000000  0.000  ...  0.000000  0.000000  0.000000  0.000000  0.000000   
175  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
176  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
177  0.901186  0.900  ... -0.746479  0.620347  0.768603  0.769817  0.559528   
178  2.553360  2.584  ... -0.746479  1.016797  1.039339  1.193458  1.068784   
..        ...    ...  ...       ...       ...       ...       ...       ...   
244  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
245  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
246  0.909091  0.920  ... -0.746479  0.987020  1.106699  1.095926  1.035390   
247  0.000000  0.000  ...  0.267606  0.000000  0.000000  0.000000  0.000000   
248  0.000000  0.000  ...  0.084507  0.000000  0.000000  0.000000  0.000000   

       X_2870  X_2871  DAY_OF_WEEK  Y_Quality  prediction_label  
174  0.000000     0.0        -0.50   0.528270          0.529161  
175  0.000000     0.0        -0.75   0.534716          0.532906  
176  0.000000     0.0         0.00   0.545925          0.552846  
177  1.193453     0.0        -1.00   0.533665          0.533681  
178  1.012566     1.0        -0.50   0.542848          0.548516  
..        ...     ...          ...        ...               ...  
244  0.000000     0.0         0.00   0.533051          0.529321  
245  0.000000     0.0        -0.75   0.534065          0.534783  
246  0.980143     1.0        -1.00   0.522340          0.525356  
247  0.000000     0.0         0.00   0.533079          0.534436  
248  0.000000     0.0         0.00   0.544089          0.539883  

[75 rows x 1394 columns]

LINE     X_128     X_129  X_132     X_133  X_134  X_135     X_136  \
174  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
175  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
176  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
177 -0.666667  1.000384  1.000000   0.95  0.952381   0.95    1.0  0.901186   
178 -0.333333  0.000000  0.000000   1.00  1.000000   0.95    1.0  2.553360   
..        ...       ...       ...    ...       ...    ...    ...       ...   
244  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
245  0.000000  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
246 -0.666667  1.524882  1.524297   0.95  0.952381   0.95    1.0  0.909091   
247  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   
248  0.333333  0.000000  0.000000   0.00  0.000000   0.00    0.0  0.000000   

        X_137  X_138  ...    X_2865    X_2866    X_2867    X_2868    X_2869  \
174  0.000000  0.000  ...  0.000000  0.000000  0.000000  0.000000  0.000000   
175  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
176  0.000000  0.000  ...  0.098592  0.000000  0.000000  0.000000  0.000000   
177  0.901186  0.900  ... -0.746479  0.620347  0.768603  0.769817  0.559528   
178  2.553360  2.584  ... -0.746479  1.016797  1.039339  1.193458  1.068784   
..        ...    ...  ...       ...       ...       ...       ...       ...   
244  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
245  0.000000  0.000  ...  0.239437  0.000000  0.000000  0.000000  0.000000   
246  0.909091  0.920  ... -0.746479  0.987020  1.106699  1.095926  1.035390   
247  0.000000  0.000  ...  0.267606  0.000000  0.000000  0.000000  0.000000   
248  0.000000  0.000  ...  0.084507  0.000000  0.000000  0.000000  0.000000   

       X_2870  X_2871  DAY_OF_WEEK  Y_Quality  prediction_label  
174  0.000000     0.0        -0.50   0.528270          0.531338  
175  0.000000     0.0        -0.75   0.534716          0.534858  
176  0.000000     0.0         0.00   0.545925          0.540877  
177  1.193453     0.0        -1.00   0.533665          0.532462  
178  1.012566     1.0        -0.50   0.542848          0.543100  
..        ...     ...          ...        ...               ...  
244  0.000000     0.0         0.00   0.533051          0.534478  
245  0.000000     0.0        -0.75   0.534065          0.534405  
246  0.980143     1.0        -1.00   0.522340          0.528193  
247  0.000000     0.0         0.00   0.533079          0.534101  
248  0.000000     0.0         0.00   0.544089          0.537212  

[75 rows x 1394 columns]

In [94]:
T05_final_regression_model = finalize_model(T05_model_gbr)

T05_prediction = predict_model(T05_final_regression_model, data=T05_data)
T05_prediction

T05_datas = T05_prediction['prediction_label']
T05_datas = pd.DataFrame(T05_datas.values, columns = ['Y_Quality'])

T05y_idx= T05_class.index
T05y_idx = pd.DataFrame(T05y_idx, columns = ['index'])
T05_datas = pd.concat([T05y_idx, T05_datas], axis = 1)
T05_datas = T05_datas.set_index('index')
T05_datas

Y_Quality
index           
0       0.532421
1       0.541788
2       0.532249
3       0.537547
4       0.531817
...          ...
583     0.523360
584     0.521043
585     0.515984
594     0.523876
595     0.522376

[249 rows x 1 columns]

In [95]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T05_datas, 
                   target=T05_class, 
                   fold=5,
                   session_id=4)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [96]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbc = create_model('gbc', fold = 5)
T05_total_models.append(T05_model_gbc)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [97]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbc = tune_model(T05_model_gbc, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [98]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbc, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]

for model in T05_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
174   0.534193        1                 1            0.6739
175   0.529732        1                 1            0.9991
176   0.521964        0                 0            0.9948
177   0.526275        0                 0            0.6639
178   0.536968        2                 2            0.9790
..         ...      ...               ...               ...
244   0.532459        1                 1            0.9983
245   0.531313        1                 1            0.9991
246   0.525242        1                 0            0.9913
247   0.532372        1                 1            0.9983
248   0.523235        0                 0            0.9934

[75 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
174   0.534193        1                 1            0.7710
175   0.529732        1                 1            0.9631
176   0.521964        0                 0            0.9609
177   0.526275        0                 0            0.6019
178   0.536968        2                 2            0.9839
..         ...      ...               ...               ...
244   0.532459        1                 1            0.9631
245   0.531313        1                 1            0.9631
246   0.525242        1                 0            0.8886
247   0.532372        1                 1            0.9631
248   0.523235        0                 0            0.9609

[75 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
174   0.534193        1                 2            0.4952
175   0.529732        1                 1            0.9781
176   0.521964        0                 0            0.9626
177   0.526275        0                 0            0.6898
178   0.536968        2                 2            0.9674
..         ...      ...               ...               ...
244   0.532459        1                 1            0.9781
245   0.531313        1                 1            0.9781
246   0.525242        1                 0            0.9626
247   0.532372        1                 1            0.9781
248   0.523235        0                 0            0.9626

[75 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
174   0.534193        1                 2            0.3848
175   0.529732        1                 1            0.4563
176   0.521964        0                 0            0.5095
177   0.526275        0                 0            0.4041
178   0.536968        2                 2            0.4825
..         ...      ...               ...               ...
244   0.532459        1                 1            0.4507
245   0.531313        1                 1            0.4617
246   0.525242        1                 0            0.4456
247   0.532372        1                 1            0.4507
248   0.523235        0                 0            0.4879

[75 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
174   0.534193        1                 1            0.3333
175   0.529732        1                 1            0.3333
176   0.521964        0                 0            0.3333
177   0.526275        0                 0            0.3333
178   0.536968        2                 2            0.3333
..         ...      ...               ...               ...
244   0.532459        1                 1            0.3333
245   0.531313        1                 1            0.3333
246   0.525242        1                 0            0.3333
247   0.532372        1                 1            0.3333
248   0.523235        0                 0            0.3333

[75 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
174   0.534193        1                 1            0.5163
175   0.529732        1                 1            0.7546
176   0.521964        0                 0            0.7239
177   0.526275        0                 0            0.4580
178   0.536968        2                 2            0.7285
..         ...      ...               ...               ...
244   0.532459        1                 1            0.7531
245   0.531313        1                 1            0.7542
246   0.525242        1                 0            0.6371
247   0.532372        1                 1            0.7531
248   0.523235        0                 0            0.7211

[75 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
174   0.534193        1                 1            0.5063
175   0.529732        1                 1            1.0000
176   0.521964        0                 0            0.5161
177   0.526275        0                 0            0.5161
178   0.536968        2                 2            0.5128
..         ...      ...               ...               ...
244   0.532459        1                 1            1.0000
245   0.531313        1                 1            1.0000
246   0.525242        1                 0            0.5161
247   0.532372        1                 1            1.0000
248   0.523235        0                 0            0.5161

[75 rows x 4 columns]

In [99]:
T05_final_classification_model = finalize_model(T05_model_catboost)

T05_prediction = predict_model(T05_final_classification_model, data=T05_datas)

T05_y_class = pd.DataFrame(T05_class, columns = ['Y_Class'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_prediction = pd.concat([T05_prediction, T05_y_class], axis = 1)
T05_prediction = T05_prediction.set_index('index')
T05_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# T_31

In [100]:
T01_class = T01['Y_Class']
T01_target = T01['Y_Quality']
T01_data = T01.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [101]:
T_01c = T01_data.columns
T_01scaler = RobustScaler()
T_01scaled = T_01scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)

T01_y_class = pd.DataFrame(T01_target, columns = ['Y_Quality'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_data = pd.concat([T01_data, T01_y_class], axis = 1)
T01_data = T01_data.set_index('index')
T01_data.drop(['Y_Quality'], axis = 1, inplace = True)
T01_data

LINE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12      X_13  \
index                                                                          
22      0.0  0.0  1.4  1.0  0.000000  0.0  0.0  0.651685  0.733624  0.720721   
23      0.0  0.0  1.4  1.0  0.000000  0.0  0.0  0.660674  0.755459  0.729730   
25      0.0  0.0  0.4  1.0  0.000000  0.0  0.0  0.786517  0.903930  0.860360   
26      1.0  0.0  0.0  0.0  1.500000  0.0  1.0 -1.011236 -1.000000 -0.882883   
29      0.0  0.0  1.0  1.0  0.000000  0.0  0.0  0.746067  0.903930  0.797297   
...     ...  ...  ...  ...       ...  ...  ...       ...       ...       ...   
589     1.0 -1.0 -0.2  0.0  0.833333  0.0  1.0 -1.546067 -1.532751 -1.518018   
590     1.0 -1.0 -1.2  0.0  0.833333  0.0  1.0 -1.523596 -1.519651 -1.432432   
591     1.0 -1.0 -1.6  0.0  0.833333  0.0  1.0 -1.528090 -1.519651 -1.486486   
592     0.0  0.0  0.6  0.0  0.000000  0.0  0.0  0.251685  0.231441  0.405405   
593     1.0  0.0  0.0  0.0  0.833333  0.0  1.0 -1.393258 -1.371179 -1.378378   

       ...      X_925      X_926  X_927  X_928      X_929      X_930  X_931  \
index  ...                                                                    
22     ...   0.613636   0.978010   0.70    0.0   0.398618   0.117647    1.0   
23     ... -36.386364 -45.896269 -29.48  -32.6 -38.797235 -34.000000 -136.0   
25     ...  -0.681818   0.035581   0.70    0.1   0.596774   1.058824    1.0   
26     ...  -0.363636  -0.852032  -0.18    0.1   0.947005   1.176471    1.0   
29     ...   0.272727   0.621234   0.34    0.1   0.755760   1.058824    1.0   
...    ...        ...        ...    ...    ...        ...        ...    ...   
589    ...  -0.045455   0.105783   0.34    0.0   0.649770   1.058824    1.0   
590    ...  -0.454545   0.255802   0.52    0.1   0.919355   1.176471    0.0   
591    ...  -0.113636   0.245224   0.06    0.0   0.928571   1.058824    0.0   
592    ...  -0.795455  -0.423131   0.04    0.0   0.801843   1.058824    0.0   
593    ...   0.250000   0.442364   0.32    0.1   0.914747   1.058824    0.0   

            X_932  X_933  DAY_OF_WEEK  
index                                  
22       0.631195    0.0    -0.857143  
23    -181.618066  -13.2    -0.857143  
25       0.787172    0.0     0.571429  
26       0.874636    0.1     0.571429  
29       0.349854    0.0     0.571429  
...           ...    ...          ...  
589      1.180758    0.1    -0.857143  
590     -0.043732    0.0    -0.571429  
591      0.043732    0.0    -0.571429  
592     -0.481050    0.0    -0.285714  
593     -0.612245    0.0    -0.285714  

[343 rows x 573 columns]

In [102]:
from pycaret.regression import *
setup_rgs = setup(data = T01_data, target = T01_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [103]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbr = create_model('gbr', fold = 5)
T01_total_models.append(T01_model_gbr)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [104]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbr = tune_model(T01_model_gbr, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [105]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbr, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]

for model in T01_tuned_models:
    display(predict_model(model))

LINE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12      X_13  \
240   0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.283146 -0.292576 -0.121622   
241   0.0  0.0  1.2  0.0  0.000000  0.0  0.0 -0.692135 -0.668122 -0.531532   
242   1.0  0.0 -0.8  0.0  1.000000  1.0  1.0 -0.148315 -0.056769 -0.198198   
243   0.0  0.0  0.8  0.0  0.000000  0.0  0.0  1.074157  1.222707  1.126126   
244   1.0  0.0 -0.6  0.0  1.500000  0.0  1.0 -0.278652 -0.192140 -0.310811   
..    ...  ...  ...  ...       ...  ...  ...       ...       ...       ...   
338   1.0 -1.0  0.0  0.0  0.833333  0.0  1.0 -1.788764 -1.786026 -1.707207   
339   1.0  0.0 -1.4  0.0  1.000000  0.0  1.0  0.462921  0.541485  0.396396   
340   1.0  0.0  0.2  0.0  0.833333  0.0  1.0  0.417978  0.497817  0.328829   
341   1.0 -1.0 -1.2  0.0  0.833333  0.0  1.0  0.494382  0.606987  0.405405   
342   1.0  0.0 -1.2  0.0  0.833333  0.0  1.0  0.458427  0.541485  0.396396   

     ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
240  ...  -2.04   -0.3 -0.142857  0.117647    1.0 -0.543732   -0.1   
241  ...  -0.12    0.1  0.801843  1.058824    1.0  1.311953    0.1   
242  ...  -0.34   -0.9 -0.412442 -0.117647    0.0  0.586006    0.0   
243  ...   0.70    0.0  0.516129  0.117647    0.0 -0.272595    0.0   
244  ...  -0.62    0.1  0.785714  1.058824    0.0  0.087464    0.0   
..   ...    ...    ...       ...       ...    ...       ...    ...   
338  ...  -0.24    0.0  0.216590  0.000000    1.0 -0.393586    0.0   
339  ...   0.54   -1.0 -1.431217 -1.058824    1.0  0.134111    0.0   
340  ...  -1.46   -0.9 -0.347926 -0.117647    1.0  0.918367    0.0   
341  ...   0.06   -0.9 -0.331797  0.117647    0.0 -0.905248    0.0   
342  ...  -0.90   -0.9 -1.039171 -0.941176    0.0  0.000000    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
240    -0.571429   0.526314          0.530261  
241    -0.857143   0.532405          0.530261  
242     0.571429   0.533146          0.530261  
243     0.571429   0.530981          0.530261  
244    -1.142857   0.528617          0.530261  
..           ...        ...               ...  
338    -0.857143   0.534122          0.530261  
339     0.571429   0.533924          0.530261  
340    -1.142857   0.534308          0.530261  
341    -0.857143   0.529013          0.530261  
342    -1.142857   0.533894          0.530261  

[103 rows x 575 columns]

LINE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12      X_13  \
240   0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.283146 -0.292576 -0.121622   
241   0.0  0.0  1.2  0.0  0.000000  0.0  0.0 -0.692135 -0.668122 -0.531532   
242   1.0  0.0 -0.8  0.0  1.000000  1.0  1.0 -0.148315 -0.056769 -0.198198   
243   0.0  0.0  0.8  0.0  0.000000  0.0  0.0  1.074157  1.222707  1.126126   
244   1.0  0.0 -0.6  0.0  1.500000  0.0  1.0 -0.278652 -0.192140 -0.310811   
..    ...  ...  ...  ...       ...  ...  ...       ...       ...       ...   
338   1.0 -1.0  0.0  0.0  0.833333  0.0  1.0 -1.788764 -1.786026 -1.707207   
339   1.0  0.0 -1.4  0.0  1.000000  0.0  1.0  0.462921  0.541485  0.396396   
340   1.0  0.0  0.2  0.0  0.833333  0.0  1.0  0.417978  0.497817  0.328829   
341   1.0 -1.0 -1.2  0.0  0.833333  0.0  1.0  0.494382  0.606987  0.405405   
342   1.0  0.0 -1.2  0.0  0.833333  0.0  1.0  0.458427  0.541485  0.396396   

     ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
240  ...  -2.04   -0.3 -0.142857  0.117647    1.0 -0.543732   -0.1   
241  ...  -0.12    0.1  0.801843  1.058824    1.0  1.311953    0.1   
242  ...  -0.34   -0.9 -0.412442 -0.117647    0.0  0.586006    0.0   
243  ...   0.70    0.0  0.516129  0.117647    0.0 -0.272595    0.0   
244  ...  -0.62    0.1  0.785714  1.058824    0.0  0.087464    0.0   
..   ...    ...    ...       ...       ...    ...       ...    ...   
338  ...  -0.24    0.0  0.216590  0.000000    1.0 -0.393586    0.0   
339  ...   0.54   -1.0 -1.431217 -1.058824    1.0  0.134111    0.0   
340  ...  -1.46   -0.9 -0.347926 -0.117647    1.0  0.918367    0.0   
341  ...   0.06   -0.9 -0.331797  0.117647    0.0 -0.905248    0.0   
342  ...  -0.90   -0.9 -1.039171 -0.941176    0.0  0.000000    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
240    -0.571429   0.526314          0.531174  
241    -0.857143   0.532405          0.529532  
242     0.571429   0.533146          0.530616  
243     0.571429   0.530981          0.530058  
244    -1.142857   0.528617          0.529930  
..           ...        ...               ...  
338    -0.857143   0.534122          0.525440  
339     0.571429   0.533924          0.527313  
340    -1.142857   0.534308          0.526581  
341    -0.857143   0.529013          0.529576  
342    -1.142857   0.533894          0.528696  

[103 rows x 575 columns]

LINE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12      X_13  \
240   0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.283146 -0.292576 -0.121622   
241   0.0  0.0  1.2  0.0  0.000000  0.0  0.0 -0.692135 -0.668122 -0.531532   
242   1.0  0.0 -0.8  0.0  1.000000  1.0  1.0 -0.148315 -0.056769 -0.198198   
243   0.0  0.0  0.8  0.0  0.000000  0.0  0.0  1.074157  1.222707  1.126126   
244   1.0  0.0 -0.6  0.0  1.500000  0.0  1.0 -0.278652 -0.192140 -0.310811   
..    ...  ...  ...  ...       ...  ...  ...       ...       ...       ...   
338   1.0 -1.0  0.0  0.0  0.833333  0.0  1.0 -1.788764 -1.786026 -1.707207   
339   1.0  0.0 -1.4  0.0  1.000000  0.0  1.0  0.462921  0.541485  0.396396   
340   1.0  0.0  0.2  0.0  0.833333  0.0  1.0  0.417978  0.497817  0.328829   
341   1.0 -1.0 -1.2  0.0  0.833333  0.0  1.0  0.494382  0.606987  0.405405   
342   1.0  0.0 -1.2  0.0  0.833333  0.0  1.0  0.458427  0.541485  0.396396   

     ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
240  ...  -2.04   -0.3 -0.142857  0.117647    1.0 -0.543732   -0.1   
241  ...  -0.12    0.1  0.801843  1.058824    1.0  1.311953    0.1   
242  ...  -0.34   -0.9 -0.412442 -0.117647    0.0  0.586006    0.0   
243  ...   0.70    0.0  0.516129  0.117647    0.0 -0.272595    0.0   
244  ...  -0.62    0.1  0.785714  1.058824    0.0  0.087464    0.0   
..   ...    ...    ...       ...       ...    ...       ...    ...   
338  ...  -0.24    0.0  0.216590  0.000000    1.0 -0.393586    0.0   
339  ...   0.54   -1.0 -1.431217 -1.058824    1.0  0.134111    0.0   
340  ...  -1.46   -0.9 -0.347926 -0.117647    1.0  0.918367    0.0   
341  ...   0.06   -0.9 -0.331797  0.117647    0.0 -0.905248    0.0   
342  ...  -0.90   -0.9 -1.039171 -0.941176    0.0  0.000000    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
240    -0.571429   0.526314          0.530757  
241    -0.857143   0.532405          0.530525  
242     0.571429   0.533146          0.531535  
243     0.571429   0.530981          0.531184  
244    -1.142857   0.528617          0.531808  
..           ...        ...               ...  
338    -0.857143   0.534122          0.528143  
339     0.571429   0.533924          0.528238  
340    -1.142857   0.534308          0.530746  
341    -0.857143   0.529013          0.530678  
342    -1.142857   0.533894          0.526761  

[103 rows x 575 columns]

LINE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12      X_13  \
240   0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.283146 -0.292576 -0.121622   
241   0.0  0.0  1.2  0.0  0.000000  0.0  0.0 -0.692135 -0.668122 -0.531532   
242   1.0  0.0 -0.8  0.0  1.000000  1.0  1.0 -0.148315 -0.056769 -0.198198   
243   0.0  0.0  0.8  0.0  0.000000  0.0  0.0  1.074157  1.222707  1.126126   
244   1.0  0.0 -0.6  0.0  1.500000  0.0  1.0 -0.278652 -0.192140 -0.310811   
..    ...  ...  ...  ...       ...  ...  ...       ...       ...       ...   
338   1.0 -1.0  0.0  0.0  0.833333  0.0  1.0 -1.788764 -1.786026 -1.707207   
339   1.0  0.0 -1.4  0.0  1.000000  0.0  1.0  0.462921  0.541485  0.396396   
340   1.0  0.0  0.2  0.0  0.833333  0.0  1.0  0.417978  0.497817  0.328829   
341   1.0 -1.0 -1.2  0.0  0.833333  0.0  1.0  0.494382  0.606987  0.405405   
342   1.0  0.0 -1.2  0.0  0.833333  0.0  1.0  0.458427  0.541485  0.396396   

     ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
240  ...  -2.04   -0.3 -0.142857  0.117647    1.0 -0.543732   -0.1   
241  ...  -0.12    0.1  0.801843  1.058824    1.0  1.311953    0.1   
242  ...  -0.34   -0.9 -0.412442 -0.117647    0.0  0.586006    0.0   
243  ...   0.70    0.0  0.516129  0.117647    0.0 -0.272595    0.0   
244  ...  -0.62    0.1  0.785714  1.058824    0.0  0.087464    0.0   
..   ...    ...    ...       ...       ...    ...       ...    ...   
338  ...  -0.24    0.0  0.216590  0.000000    1.0 -0.393586    0.0   
339  ...   0.54   -1.0 -1.431217 -1.058824    1.0  0.134111    0.0   
340  ...  -1.46   -0.9 -0.347926 -0.117647    1.0  0.918367    0.0   
341  ...   0.06   -0.9 -0.331797  0.117647    0.0 -0.905248    0.0   
342  ...  -0.90   -0.9 -1.039171 -0.941176    0.0  0.000000    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
240    -0.571429   0.526314          0.528075  
241    -0.857143   0.532405          0.529602  
242     0.571429   0.533146          0.532341  
243     0.571429   0.530981          0.530488  
244    -1.142857   0.528617          0.528956  
..           ...        ...               ...  
338    -0.857143   0.534122          0.528420  
339     0.571429   0.533924          0.529896  
340    -1.142857   0.534308          0.528915  
341    -0.857143   0.529013          0.529415  
342    -1.142857   0.533894          0.528151  

[103 rows x 575 columns]

LINE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12      X_13  \
240   0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.283146 -0.292576 -0.121622   
241   0.0  0.0  1.2  0.0  0.000000  0.0  0.0 -0.692135 -0.668122 -0.531532   
242   1.0  0.0 -0.8  0.0  1.000000  1.0  1.0 -0.148315 -0.056769 -0.198198   
243   0.0  0.0  0.8  0.0  0.000000  0.0  0.0  1.074157  1.222707  1.126126   
244   1.0  0.0 -0.6  0.0  1.500000  0.0  1.0 -0.278652 -0.192140 -0.310811   
..    ...  ...  ...  ...       ...  ...  ...       ...       ...       ...   
338   1.0 -1.0  0.0  0.0  0.833333  0.0  1.0 -1.788764 -1.786026 -1.707207   
339   1.0  0.0 -1.4  0.0  1.000000  0.0  1.0  0.462921  0.541485  0.396396   
340   1.0  0.0  0.2  0.0  0.833333  0.0  1.0  0.417978  0.497817  0.328829   
341   1.0 -1.0 -1.2  0.0  0.833333  0.0  1.0  0.494382  0.606987  0.405405   
342   1.0  0.0 -1.2  0.0  0.833333  0.0  1.0  0.458427  0.541485  0.396396   

     ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
240  ...  -2.04   -0.3 -0.142857  0.117647    1.0 -0.543732   -0.1   
241  ...  -0.12    0.1  0.801843  1.058824    1.0  1.311953    0.1   
242  ...  -0.34   -0.9 -0.412442 -0.117647    0.0  0.586006    0.0   
243  ...   0.70    0.0  0.516129  0.117647    0.0 -0.272595    0.0   
244  ...  -0.62    0.1  0.785714  1.058824    0.0  0.087464    0.0   
..   ...    ...    ...       ...       ...    ...       ...    ...   
338  ...  -0.24    0.0  0.216590  0.000000    1.0 -0.393586    0.0   
339  ...   0.54   -1.0 -1.431217 -1.058824    1.0  0.134111    0.0   
340  ...  -1.46   -0.9 -0.347926 -0.117647    1.0  0.918367    0.0   
341  ...   0.06   -0.9 -0.331797  0.117647    0.0 -0.905248    0.0   
342  ...  -0.90   -0.9 -1.039171 -0.941176    0.0  0.000000    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
240    -0.571429   0.526314          0.529434  
241    -0.857143   0.532405          0.529569  
242     0.571429   0.533146          0.531096  
243     0.571429   0.530981          0.531322  
244    -1.142857   0.528617          0.528675  
..           ...        ...               ...  
338    -0.857143   0.534122          0.527590  
339     0.571429   0.533924          0.529929  
340    -1.142857   0.534308          0.528694  
341    -0.857143   0.529013          0.530751  
342    -1.142857   0.533894          0.528269  

[103 rows x 575 columns]

LINE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12      X_13  \
240   0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.283146 -0.292576 -0.121622   
241   0.0  0.0  1.2  0.0  0.000000  0.0  0.0 -0.692135 -0.668122 -0.531532   
242   1.0  0.0 -0.8  0.0  1.000000  1.0  1.0 -0.148315 -0.056769 -0.198198   
243   0.0  0.0  0.8  0.0  0.000000  0.0  0.0  1.074157  1.222707  1.126126   
244   1.0  0.0 -0.6  0.0  1.500000  0.0  1.0 -0.278652 -0.192140 -0.310811   
..    ...  ...  ...  ...       ...  ...  ...       ...       ...       ...   
338   1.0 -1.0  0.0  0.0  0.833333  0.0  1.0 -1.788764 -1.786026 -1.707207   
339   1.0  0.0 -1.4  0.0  1.000000  0.0  1.0  0.462921  0.541485  0.396396   
340   1.0  0.0  0.2  0.0  0.833333  0.0  1.0  0.417978  0.497817  0.328829   
341   1.0 -1.0 -1.2  0.0  0.833333  0.0  1.0  0.494382  0.606987  0.405405   
342   1.0  0.0 -1.2  0.0  0.833333  0.0  1.0  0.458427  0.541485  0.396396   

     ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
240  ...  -2.04   -0.3 -0.142857  0.117647    1.0 -0.543732   -0.1   
241  ...  -0.12    0.1  0.801843  1.058824    1.0  1.311953    0.1   
242  ...  -0.34   -0.9 -0.412442 -0.117647    0.0  0.586006    0.0   
243  ...   0.70    0.0  0.516129  0.117647    0.0 -0.272595    0.0   
244  ...  -0.62    0.1  0.785714  1.058824    0.0  0.087464    0.0   
..   ...    ...    ...       ...       ...    ...       ...    ...   
338  ...  -0.24    0.0  0.216590  0.000000    1.0 -0.393586    0.0   
339  ...   0.54   -1.0 -1.431217 -1.058824    1.0  0.134111    0.0   
340  ...  -1.46   -0.9 -0.347926 -0.117647    1.0  0.918367    0.0   
341  ...   0.06   -0.9 -0.331797  0.117647    0.0 -0.905248    0.0   
342  ...  -0.90   -0.9 -1.039171 -0.941176    0.0  0.000000    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
240    -0.571429   0.526314          0.529073  
241    -0.857143   0.532405          0.527516  
242     0.571429   0.533146          0.530455  
243     0.571429   0.530981          0.531129  
244    -1.142857   0.528617          0.531125  
..           ...        ...               ...  
338    -0.857143   0.534122          0.525332  
339     0.571429   0.533924          0.526813  
340    -1.142857   0.534308          0.528869  
341    -0.857143   0.529013          0.528586  
342    -1.142857   0.533894          0.528210  

[103 rows x 575 columns]

LINE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12      X_13  \
240   0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.283146 -0.292576 -0.121622   
241   0.0  0.0  1.2  0.0  0.000000  0.0  0.0 -0.692135 -0.668122 -0.531532   
242   1.0  0.0 -0.8  0.0  1.000000  1.0  1.0 -0.148315 -0.056769 -0.198198   
243   0.0  0.0  0.8  0.0  0.000000  0.0  0.0  1.074157  1.222707  1.126126   
244   1.0  0.0 -0.6  0.0  1.500000  0.0  1.0 -0.278652 -0.192140 -0.310811   
..    ...  ...  ...  ...       ...  ...  ...       ...       ...       ...   
338   1.0 -1.0  0.0  0.0  0.833333  0.0  1.0 -1.788764 -1.786026 -1.707207   
339   1.0  0.0 -1.4  0.0  1.000000  0.0  1.0  0.462921  0.541485  0.396396   
340   1.0  0.0  0.2  0.0  0.833333  0.0  1.0  0.417978  0.497817  0.328829   
341   1.0 -1.0 -1.2  0.0  0.833333  0.0  1.0  0.494382  0.606987  0.405405   
342   1.0  0.0 -1.2  0.0  0.833333  0.0  1.0  0.458427  0.541485  0.396396   

     ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
240  ...  -2.04   -0.3 -0.142857  0.117647    1.0 -0.543732   -0.1   
241  ...  -0.12    0.1  0.801843  1.058824    1.0  1.311953    0.1   
242  ...  -0.34   -0.9 -0.412442 -0.117647    0.0  0.586006    0.0   
243  ...   0.70    0.0  0.516129  0.117647    0.0 -0.272595    0.0   
244  ...  -0.62    0.1  0.785714  1.058824    0.0  0.087464    0.0   
..   ...    ...    ...       ...       ...    ...       ...    ...   
338  ...  -0.24    0.0  0.216590  0.000000    1.0 -0.393586    0.0   
339  ...   0.54   -1.0 -1.431217 -1.058824    1.0  0.134111    0.0   
340  ...  -1.46   -0.9 -0.347926 -0.117647    1.0  0.918367    0.0   
341  ...   0.06   -0.9 -0.331797  0.117647    0.0 -0.905248    0.0   
342  ...  -0.90   -0.9 -1.039171 -0.941176    0.0  0.000000    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
240    -0.571429   0.526314          0.530149  
241    -0.857143   0.532405          0.530156  
242     0.571429   0.533146          0.530216  
243     0.571429   0.530981          0.530170  
244    -1.142857   0.528617          0.530149  
..           ...        ...               ...  
338    -0.857143   0.534122          0.530055  
339     0.571429   0.533924          0.530115  
340    -1.142857   0.534308          0.530139  
341    -0.857143   0.529013          0.530167  
342    -1.142857   0.533894          0.530149  

[103 rows x 575 columns]

In [106]:
T01_final_regression_model = finalize_model(T01_model_et)

T01_prediction = predict_model(T01_final_regression_model, data=T01_data)

T01_datas = T01_prediction['prediction_label']
T01_datas = pd.DataFrame(T01_datas.values, columns = ['Y_Quality'])

T01y_idx= T01_class.index
T01y_idx = pd.DataFrame(T01y_idx, columns = ['index'])
T01_datas = pd.concat([T01y_idx, T01_datas], axis = 1)
T01_datas = T01_datas.set_index('index')
T01_datas

Y_Quality
index           
22      0.517719
23      0.519090
25      0.529362
26      0.531992
29      0.532405
...          ...
589     0.529510
590     0.529948
591     0.529308
592     0.528349
593     0.526546

[343 rows x 1 columns]

In [107]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T01_datas, 
                   target=T01_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [108]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbc = create_model('gbc', fold = 5)
T01_total_models.append(T01_model_gbc)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [109]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbc = tune_model(T01_model_gbc, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [110]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbc, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]

for model in T01_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
240   0.530317        1                 1            0.9997
241   0.529362        1                 1            0.9997
242   0.528349        1                 1            0.9997
243   0.530413        1                 1            0.9997
244   0.519090        0                 0            0.9996
..         ...      ...               ...               ...
338   0.529633        1                 1            0.9997
339   0.531035        1                 1            0.9997
340   0.532084        1                 1            0.9997
341   0.530506        1                 1            0.9997
342   0.528751        1                 1            0.9997

[103 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
240   0.530317        1                 1               1.0
241   0.529362        1                 1               1.0
242   0.528349        1                 1               1.0
243   0.530413        1                 1               1.0
244   0.519090        0                 0               1.0
..         ...      ...               ...               ...
338   0.529633        1                 1               1.0
339   0.531035        1                 1               1.0
340   0.532084        1                 1               1.0
341   0.530506        1                 1               1.0
342   0.528751        1                 1               1.0

[103 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
240   0.530317        1                 1               1.0
241   0.529362        1                 1               1.0
242   0.528349        1                 1               1.0
243   0.530413        1                 1               1.0
244   0.519090        0                 0               1.0
..         ...      ...               ...               ...
338   0.529633        1                 1               1.0
339   0.531035        1                 1               1.0
340   0.532084        1                 1               1.0
341   0.530506        1                 1               1.0
342   0.528751        1                 1               1.0

[103 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
240   0.530317        1                 1               1.0
241   0.529362        1                 1               1.0
242   0.528349        1                 1               1.0
243   0.530413        1                 1               1.0
244   0.519090        0                 0               1.0
..         ...      ...               ...               ...
338   0.529633        1                 1               1.0
339   0.531035        1                 1               1.0
340   0.532084        1                 1               1.0
341   0.530506        1                 1               1.0
342   0.528751        1                 1               1.0

[103 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
240   0.530317        1                 1            0.9999
241   0.529362        1                 1            0.9999
242   0.528349        1                 1            0.9999
243   0.530413        1                 1            0.9999
244   0.519090        0                 0            0.9985
..         ...      ...               ...               ...
338   0.529633        1                 1            0.9999
339   0.531035        1                 1            0.9999
340   0.532084        1                 1            0.9999
341   0.530506        1                 1            0.9999
342   0.528751        1                 1            0.9999

[103 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
240   0.530317        1                 1            0.9991
241   0.529362        1                 1            0.9991
242   0.528349        1                 1            0.9991
243   0.530413        1                 1            0.9991
244   0.519090        0                 0            0.9814
..         ...      ...               ...               ...
338   0.529633        1                 1            0.9991
339   0.531035        1                 1            0.9991
340   0.532084        1                 1            0.9991
341   0.530506        1                 1            0.9991
342   0.528751        1                 1            0.9991

[103 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
240   0.530317        1                 1               1.0
241   0.529362        1                 1               1.0
242   0.528349        1                 1               1.0
243   0.530413        1                 1               1.0
244   0.519090        0                 0               1.0
..         ...      ...               ...               ...
338   0.529633        1                 1               1.0
339   0.531035        1                 1               1.0
340   0.532084        1                 1               1.0
341   0.530506        1                 1               1.0
342   0.528751        1                 1               1.0

[103 rows x 4 columns]

In [111]:
T01_final_classification_model = finalize_model(T01_model_gbc)

T01_prediction = predict_model(T01_final_classification_model, data=T01_datas)

T01_prediction = pd.DataFrame(T01_prediction, columns = ['prediction_label'])

T01_y_class = pd.DataFrame(T01_class, columns = ['Y_Class'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_prediction = pd.concat([T01_prediction, T01_y_class], axis = 1)
T01_prediction = T01_prediction.set_index('index')
T01_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# O_31

In [112]:
T10.drop(['index'], inplace = True, axis = 1)

In [113]:
T10_class = T10['Y_Class']
T10_target = T10['Y_Quality']
T10_data = T10.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [114]:
T_10c = T10_data.columns
T_10scaler = RobustScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)

T10_y_class = pd.DataFrame(T10_target, columns = ['Y_Quality'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_data = pd.concat([T10_data, T10_y_class], axis = 1)
T10_data = T10_data.set_index('index')
T10_data.drop(['Y_Quality'], axis = 1, inplace = True)
T10_data

LINE       X_1       X_2  X_5       X_7  X_9      X_11      X_12  \
index                                                                     
0      -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
1       0.5  0.000000 -0.222222 -0.5  0.500000  0.5 -0.559767 -0.544248   
2      -0.5 -0.117647  0.888889  0.5 -0.500000 -0.5  0.440233  0.441003   
3       0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
4      -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
5       0.5  0.882353 -0.555556 -0.5  2.166667  0.5 -0.428571 -0.441003   
6      -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
7       0.5  0.000000 -0.222222 -0.5  0.500000  0.5 -0.559767 -0.544248   
8      -0.5 -0.117647  0.888889  0.5 -0.500000 -0.5  0.440233  0.441003   
9       0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
10     -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
11      0.5  0.882353 -0.555556 -0.5  2.166667  0.5 -0.428571 -0.441003   
12     -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
13      0.5  0.000000 -0.222222 -0.5  0.500000  0.5 -0.559767 -0.544248   
14     -0.5 -0.117647  0.888889  0.5 -0.500000 -0.5  0.440233  0.441003   
15      0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
16     -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
17      0.5  0.882353 -0.555556 -0.5  2.166667  0.5 -0.428571 -0.441003   
18     -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
19      0.5  0.000000 -0.222222 -0.5  0.500000  0.5 -0.559767 -0.544248   
20     -0.5 -0.117647  0.888889  0.5 -0.500000 -0.5  0.440233  0.441003   
21      0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
22     -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
23      0.5  0.882353 -0.555556 -0.5  2.166667  0.5 -0.428571 -0.441003   

           X_13  X_16  ...     X_925     X_926     X_927  X_928     X_929  \
index                  ...                                                  
0      0.433148   1.0  ... -0.531818 -0.510638 -0.274336    1.0  0.016667   
1     -0.575209   1.0  ... -0.359091 -0.310839  0.141593    1.0  0.073810   
2      0.410864   0.0  ... -0.013636 -0.061426 -0.371681    0.0 -0.016667   
3     -0.566852   0.0  ...  0.013636  0.061426 -0.141593    0.0  0.084612   
4      0.541783   0.0  ...  1.240909  1.323422  1.389381   -5.0 -1.159524   
5     -0.410864   0.0  ...  0.640909  0.689161  0.725664    0.0 -0.926190   
6      0.433148   1.0  ... -0.531818 -0.510638 -0.274336    1.0  0.016667   
7     -0.575209   1.0  ... -0.359091 -0.310839  0.141593    1.0  0.073810   
8      0.410864   0.0  ... -0.013636 -0.061426 -0.371681    0.0 -0.016667   
9     -0.566852   0.0  ...  0.013636  0.061426 -0.141593    0.0  0.084612   
10     0.541783   0.0  ...  1.240909  1.323422  1.389381   -5.0 -1.159524   
11    -0.410864   0.0  ...  0.640909  0.689161  0.725664    0.0 -0.926190   
12     0.433148   1.0  ... -0.531818 -0.510638 -0.274336    1.0  0.016667   
13    -0.575209   1.0  ... -0.359091 -0.310839  0.141593    1.0  0.073810   
14     0.410864   0.0  ... -0.013636 -0.061426 -0.371681    0.0 -0.016667   
15    -0.566852   0.0  ...  0.013636  0.061426 -0.141593    0.0  0.084612   
16     0.541783   0.0  ...  1.240909  1.323422  1.389381   -5.0 -1.159524   
17    -0.410864   0.0  ...  0.640909  0.689161  0.725664    0.0 -0.926190   
18     0.433148   1.0  ... -0.531818 -0.510638 -0.274336    1.0  0.016667   
19    -0.575209   1.0  ... -0.359091 -0.310839  0.141593    1.0  0.073810   
20     0.410864   0.0  ... -0.013636 -0.061426 -0.371681    0.0 -0.016667   
21    -0.566852   0.0  ...  0.013636  0.061426 -0.141593    0.0  0.084612   
22     0.541783   0.0  ...  1.240909  1.323422  1.389381   -5.0 -1.159524   
23    -0.410864   0.0  ...  0.640909  0.689161  0.725664    0.0 -0.926190   

       X_930  X_931     X_932  X_933  DAY_OF_WEEK  
i

In [115]:
#13
from pycaret.regression import *
setup_rgs = setup(data = T10_data, target = T10_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [116]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbr = create_model('gbr', fold = 5)
T10_total_models.append(T10_model_gbr)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [117]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbr = tune_model(T10_model_gbr, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [118]:
T10_tuned_models = [T10_model_rf, T10_model_gbr, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]

for model in T10_tuned_models:
    display(predict_model(model))

LINE       X_1       X_2  X_5       X_7  X_9      X_11      X_12  \
16  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
17   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
18  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
19   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
20  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
21  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
22  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
23   0.5  0.882353 -0.555556 -0.5  2.166667  0.5 -0.428571 -0.441003   

        X_13  X_16  ...     X_927  X_928     X_929  X_930  X_931     X_932  \
16  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
17 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
18  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
19 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
20  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
21  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
22  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
23 -0.410864   0.0  ...  0.725664    0.0 -0.926190   -1.0   -0.5 -1.098214   

    X_933  DAY_OF_WEEK  Y_Quality  prediction_label  
16    0.0         -1.0   0.531375          0.531239  
17    0.0          0.0   0.535205          0.534853  
18    1.0          0.0   0.530533          0.530157  
19    0.0          0.0   0.535205          0.534853  
20    1.0          0.0   0.530533          0.530157  
21    0.0         -1.0   0.531375          0.531239  
22    1.0          0.0   0.530533          0.530157  
23    0.0         -1.0   0.533702          0.533723  

[8 rows x 512 columns]

LINE       X_1       X_2  X_5       X_7  X_9      X_11      X_12  \
16  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
17   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
18  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
19   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
20  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
21  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
22  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
23   0.5  0.882353 -0.555556 -0.5  2.166667  0.5 -0.428571 -0.441003   

        X_13  X_16  ...     X_927  X_928     X_929  X_930  X_931     X_932  \
16  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
17 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
18  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
19 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
20  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
21  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
22  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
23 -0.410864   0.0  ...  0.725664    0.0 -0.926190   -1.0   -0.5 -1.098214   

    X_933  DAY_OF_WEEK  Y_Quality  prediction_label  
16    0.0         -1.0   0.531375          0.531375  
17    0.0          0.0   0.535205          0.535205  
18    1.0          0.0   0.530533          0.530533  
19    0.0          0.0   0.535205          0.535205  
20    1.0          0.0   0.530533          0.530533  
21    0.0         -1.0   0.531375          0.531375  
22    1.0          0.0   0.530533          0.530533  
23    0.0         -1.0   0.533702          0.533702  

[8 rows x 512 columns]

LINE       X_1       X_2  X_5       X_7  X_9      X_11      X_12  \
16  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
17   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
18  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
19   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
20  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
21  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
22  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
23   0.5  0.882353 -0.555556 -0.5  2.166667  0.5 -0.428571 -0.441003   

        X_13  X_16  ...     X_927  X_928     X_929  X_930  X_931     X_932  \
16  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
17 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
18  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
19 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
20  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
21  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
22  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
23 -0.410864   0.0  ...  0.725664    0.0 -0.926190   -1.0   -0.5 -1.098214   

    X_933  DAY_OF_WEEK  Y_Quality  prediction_label  
16    0.0         -1.0   0.531375          0.531375  
17    0.0          0.0   0.535205          0.535205  
18    1.0          0.0   0.530533          0.530533  
19    0.0          0.0   0.535205          0.535205  
20    1.0          0.0   0.530533          0.530533  
21    0.0         -1.0   0.531375          0.531375  
22    1.0          0.0   0.530533          0.530533  
23    0.0         -1.0   0.533702          0.533702  

[8 rows x 512 columns]

LINE       X_1       X_2  X_5       X_7  X_9      X_11      X_12  \
16  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
17   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
18  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
19   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
20  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
21  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
22  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
23   0.5  0.882353 -0.555556 -0.5  2.166667  0.5 -0.428571 -0.441003   

        X_13  X_16  ...     X_927  X_928     X_929  X_930  X_931     X_932  \
16  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
17 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
18  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
19 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
20  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
21  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
22  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
23 -0.410864   0.0  ...  0.725664    0.0 -0.926190   -1.0   -0.5 -1.098214   

    X_933  DAY_OF_WEEK  Y_Quality  prediction_label  
16    0.0         -1.0   0.531375          0.531375  
17    0.0          0.0   0.535205          0.535204  
18    1.0          0.0   0.530533          0.530536  
19    0.0          0.0   0.535205          0.535204  
20    1.0          0.0   0.530533          0.530536  
21    0.0         -1.0   0.531375          0.531375  
22    1.0          0.0   0.530533          0.530536  
23    0.0         -1.0   0.533702          0.533701  

[8 rows x 512 columns]

LINE       X_1       X_2  X_5       X_7  X_9      X_11      X_12  \
16  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
17   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
18  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
19   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
20  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
21  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
22  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
23   0.5  0.882353 -0.555556 -0.5  2.166667  0.5 -0.428571 -0.441003   

        X_13  X_16  ...     X_927  X_928     X_929  X_930  X_931     X_932  \
16  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
17 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
18  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
19 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
20  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
21  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
22  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
23 -0.410864   0.0  ...  0.725664    0.0 -0.926190   -1.0   -0.5 -1.098214   

    X_933  DAY_OF_WEEK  Y_Quality  prediction_label  
16    0.0         -1.0   0.531375          0.531409  
17    0.0          0.0   0.535205          0.534770  
18    1.0          0.0   0.530533          0.530539  
19    0.0          0.0   0.535205          0.534770  
20    1.0          0.0   0.530533          0.530539  
21    0.0         -1.0   0.531375          0.531409  
22    1.0          0.0   0.530533          0.530539  
23    0.0         -1.0   0.533702          0.533773  

[8 rows x 512 columns]

LINE       X_1       X_2  X_5       X_7  X_9      X_11      X_12  \
16  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
17   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
18  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
19   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
20  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
21  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
22  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
23   0.5  0.882353 -0.555556 -0.5  2.166667  0.5 -0.428571 -0.441003   

        X_13  X_16  ...     X_927  X_928     X_929  X_930  X_931     X_932  \
16  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
17 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
18  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
19 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
20  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
21  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
22  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
23 -0.410864   0.0  ...  0.725664    0.0 -0.926190   -1.0   -0.5 -1.098214   

    X_933  DAY_OF_WEEK  Y_Quality  prediction_label  
16    0.0         -1.0   0.531375          0.531375  
17    0.0          0.0   0.535205          0.535096  
18    1.0          0.0   0.530533          0.530533  
19    0.0          0.0   0.535205          0.535096  
20    1.0          0.0   0.530533          0.530533  
21    0.0         -1.0   0.531375          0.531375  
22    1.0          0.0   0.530533          0.530533  
23    0.0         -1.0   0.533702          0.533702  

[8 rows x 512 columns]

LINE       X_1       X_2  X_5       X_7  X_9      X_11      X_12  \
16  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
17   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
18  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
19   0.5  0.000000 -0.333333 -0.5  0.500000  0.5 -0.565598 -0.544248   
20  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
21  -0.5  2.000000  0.222222  0.5 -0.500000 -0.5  0.597668  0.620944   
22  -0.5 -0.117647  0.666667  0.5 -0.500000 -0.5  0.428571  0.455752   
23   0.5  0.882353 -0.555556 -0.5  2.166667  0.5 -0.428571 -0.441003   

        X_13  X_16  ...     X_927  X_928     X_929  X_930  X_931     X_932  \
16  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
17 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
18  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
19 -0.566852   0.0  ... -0.141593    0.0  0.084612    0.0    0.5  0.147321   
20  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
21  0.541783   0.0  ...  1.389381   -5.0 -1.159524   -1.0   -0.5 -0.544643   
22  0.433148   1.0  ... -0.274336    1.0  0.016667    0.0   -0.5  0.522322   
23 -0.410864   0.0  ...  0.725664    0.0 -0.926190   -1.0   -0.5 -1.098214   

    X_933  DAY_OF_WEEK  Y_Quality  prediction_label  
16    0.0         -1.0   0.531375          0.531766  
17    0.0          0.0   0.535205          0.531766  
18    1.0          0.0   0.530533          0.531766  
19    0.0          0.0   0.535205          0.531766  
20    1.0          0.0   0.530533          0.531766  
21    0.0         -1.0   0.531375          0.531766  
22    1.0          0.0   0.530533          0.531766  
23    0.0         -1.0   0.533702          0.531766  

[8 rows x 512 columns]

In [119]:
T10_final_regression_model = finalize_model(T10_model_gbr)

T10_prediction = predict_model(T10_final_regression_model, data=T10_data)

T10_datas = T10_prediction['prediction_label']
T10_datas = pd.DataFrame(T10_datas.values, columns = ['Y_Quality'])

T10y_idx= T10_class.index
T10y_idx = pd.DataFrame(T10y_idx, columns = ['index'])
T10_datas = pd.concat([T10y_idx, T10_datas], axis = 1)
T10_datas = T10_datas.set_index('index')

In [120]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T10_datas, 
                   target=T10_class, 
                   fold=5,
                   session_id=4)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [121]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbc = create_model('gbc', fold = 5)
T10_total_models.append(T10_model_gbc)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [122]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbc = tune_model(T10_model_gbc, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [123]:
T10_tuned_models = [T10_model_rf, T10_model_gbc, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]

for model in T10_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
16   0.534951        2                 2              1.00
17   0.531375        1                 1              1.00
18   0.535205        2                 2              1.00
19   0.531375        1                 1              1.00
20   0.533702        1                 1              0.92
21   0.525916        1                 1              1.00
22   0.525916        1                 1              1.00
23   0.535205        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
16   0.534951        2                 2               1.0
17   0.531375        1                 1               1.0
18   0.535205        2                 2               1.0
19   0.531375        1                 1               1.0
20   0.533702        1                 1               1.0
21   0.525916        1                 1               1.0
22   0.525916        1                 1               1.0
23   0.535205        2                 2               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
16   0.534951        2                 2               1.0
17   0.531375        1                 1               1.0
18   0.535205        2                 2               1.0
19   0.531375        1                 1               1.0
20   0.533702        1                 1               1.0
21   0.525916        1                 1               1.0
22   0.525916        1                 1               1.0
23   0.535205        2                 2               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
16   0.534951        2                 2            0.9133
17   0.531375        1                 1            0.9373
18   0.535205        2                 2            0.9030
19   0.531375        1                 1            0.9373
20   0.533702        1                 1            0.9241
21   0.525916        1                 1            0.9245
22   0.525916        1                 1            0.9245
23   0.535205        2                 2            0.9030

Y_Quality  Y_Class  prediction_label  prediction_score
16   0.534951        2                 2            0.7579
17   0.531375        1                 1            0.9060
18   0.535205        2                 2            0.7579
19   0.531375        1                 1            0.9060
20   0.533702        1                 1            0.8472
21   0.525916        1                 1            0.9060
22   0.525916        1                 1            0.9060
23   0.535205        2                 2            0.7579

Y_Quality  Y_Class  prediction_label  prediction_score
16   0.534951        2                 2               1.0
17   0.531375        1                 1               1.0
18   0.535205        2                 2               1.0
19   0.531375        1                 1               1.0
20   0.533702        1                 1               1.0
21   0.525916        1                 1               1.0
22   0.525916        1                 1               1.0
23   0.535205        2                 2               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
16   0.534951        2                 1            0.6875
17   0.531375        1                 1            0.6875
18   0.535205        2                 1            0.6875
19   0.531375        1                 1            0.6875
20   0.533702        1                 1            0.6875
21   0.525916        1                 1            0.6875
22   0.525916        1                 1            0.6875
23   0.535205        2                 1            0.6875

In [124]:
T10_final_classification_model = finalize_model(T10_model_gbc)

T10_prediction = predict_model(T10_final_classification_model, data=T10_datas)

T10_y_class = pd.DataFrame(T10_class, columns = ['Y_Class'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_prediction = pd.concat([T10_prediction, T10_y_class], axis = 1)
T10_prediction = T10_prediction.set_index('index')
T10_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# Test

In [125]:
test_data = pd.read_csv("./test.csv")
test_data

PRODUCT_ID         TIMESTAMP     LINE PRODUCT_CODE  X_1   X_2  X_3   X_4  \
0     TEST_000   2022-09-09 2:01  T100306         T_31  2.0  94.0  0.0  45.0   
1     TEST_001   2022-09-09 2:09  T100304         T_31  2.0  93.0  0.0  45.0   
2     TEST_002   2022-09-09 8:42  T100304         T_31  2.0  95.0  0.0  45.0   
3     TEST_003  2022-09-09 10:56  T010305         A_31  NaN   NaN  NaN   NaN   
4     TEST_004  2022-09-09 11:04  T010306         A_31  NaN   NaN  NaN   NaN   
..         ...               ...      ...          ...  ...   ...  ...   ...   
305   TEST_305  2022-11-05 11:18  T100306         T_31  2.0  91.0  0.0  45.0   
306   TEST_306  2022-11-05 16:39  T100304         T_31  2.0  96.0  0.0  45.0   
307   TEST_307  2022-11-05 16:47  T100306         T_31  2.0  91.0  0.0  45.0   
308   TEST_308  2022-11-05 20:53  T100306         T_31  2.0  95.0  0.0  45.0   
309   TEST_309  2022-11-05 21:01  T100306         T_31  2.0  87.0  0.0  45.0   

      X_5  X_6  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  X_2872  \
0    10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
4     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
..    ...  ...  ...     ...     ...     ...     ...     ...     ...     ...   
305  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
306  11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
307  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
308  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
309  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   

     X_2873  X_2874  X_2875  
0       NaN     NaN     NaN  
1       NaN     NaN     NaN  
2       NaN     NaN     NaN  
3       NaN     NaN     NaN  
4       NaN     NaN     NaN  
..      ...     ...     ...  
305     NaN     NaN     NaN  
306     NaN     NaN     NaN  
307     NaN     NaN     NaN  
308     NaN     NaN     NaN  
309     NaN     NaN     NaN  

[310 rows x 2879 columns]

In [126]:
test_data['YEAR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.year
test_data['MONTH'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.month
test_data['DAY'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day
test_data['HOUR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.hour
test_data['MINUTE'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.minute
test_data['DAY_OF_WEEK'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day_name()

test_data = test_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE', 'HOUR'], axis = 1)

In [127]:
test_data.drop(colls, inplace = True, axis = 1)

In [128]:
test_data.loc[test_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
test_data.loc[test_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
test_data.loc[test_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
test_data.loc[test_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
test_data.loc[test_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
test_data.loc[test_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
test_data.loc[test_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

test_data.loc[test_data.LINE == 'T050304','LINE'] = 1
test_data.loc[test_data.LINE == 'T050307','LINE'] = 2
test_data.loc[test_data.LINE == 'T010305','LINE'] = 3
test_data.loc[test_data.LINE == 'T010306','LINE'] = 4
test_data.loc[test_data.LINE == 'T100304','LINE'] = 5
test_data.loc[test_data.LINE == 'T100306','LINE'] = 6

test_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
test_data

LINE PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8  ...  \
0      6         T_31  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
1      5         T_31  2.0  93.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
2      5         T_31  2.0  95.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
3      3         A_31  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
4      4         A_31  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
..   ...          ...  ...   ...  ...   ...   ...  ...   ...   ...  ...   
305    6         T_31  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
306    5         T_31  2.0  96.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
307    6         T_31  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  ...   
308    6         T_31  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
309    6         T_31  2.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   

     X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  \
0       NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1       NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2       NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     467.0  444.192308   423.0     NaN     NaN     NaN     NaN     NaN   
4     465.0  443.211539   423.0     NaN     NaN     NaN     NaN     NaN   
..      ...         ...     ...     ...     ...     ...     ...     ...   
305     NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
306     NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
307     NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
308     NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
309     NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   

     X_2871  DAY_OF_WEEK  
0       NaN            5  
1       NaN            5  
2       NaN            5  
3       NaN            5  
4       NaN            5  
..      ...          ...  
305     NaN            6  
306     NaN            6  
307     NaN            6  
308     NaN            6  
309     NaN            6  

[310 rows x 2796 columns]

In [129]:
TT05 = test_data[test_data['PRODUCT_CODE'] == 'A_31']
TT01 = test_data[test_data['PRODUCT_CODE'] == 'T_31']
TT10 = test_data[test_data['PRODUCT_CODE'] == 'O_31']

TT05.drop(['PRODUCT_CODE'], axis = 1, inplace = True)
TT01.drop(['PRODUCT_CODE'], axis = 1, inplace = True)
TT10.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [130]:
TT05.drop(A_31_col, inplace = True, axis = 1)
TT01.drop(T_31_col, inplace = True, axis = 1)
TT10.drop(O_31_col, inplace = True, axis = 1)

In [131]:
#TT05 = TT05.fillna(T05.mean())
#TT01 = TT01.fillna(T01.mean())
#TT10 = TT10.fillna(T10.mean())

TT05 = TT05.fillna(0)
TT01 = TT01.fillna(0)
TT10 = TT10.fillna(0)

In [132]:
TT05.drop(A_31_cols, inplace = True, axis = 1)
TT01.drop(T_31_cols, inplace = True, axis = 1)
TT10.drop(O_31_cols, inplace = True, axis = 1)

In [133]:
TT05.drop(T05_75, inplace = True, axis = 1)
TT01.drop(T01_75, inplace = True, axis = 1)
TT10.drop(T10_75, inplace = True, axis = 1)

In [134]:
TT05_idx = TT05['LINE'].index
TT05_idx = pd.DataFrame(TT05_idx, columns = ['index'])

TT05c = TT05.columns
TT05scaled = T_05scaler.transform(TT05)
TT05scaled
TT05 = pd.DataFrame(TT05scaled, columns = TT05c)

TT05 = pd.concat([TT05_idx, TT05], axis = 1)
TT05 = TT05.set_index('index')

In [135]:
TT01_idx = TT01['LINE'].index
TT01_idx = pd.DataFrame(TT01_idx, columns = ['index'])

TT01c = TT01.columns
TT01scaled = T_01scaler.transform(TT01)
TT01 = pd.DataFrame(TT01scaled, columns = TT01c)

TT01 = pd.concat([TT01_idx, TT01], axis = 1)
TT01 = TT01.set_index('index')

In [136]:
TT10_idx = TT10['LINE'].index
TT10_idx = pd.DataFrame(TT10_idx, columns = ['index'])

TT10c = TT10.columns
TT10scaled = T_10scaler.transform(TT10)
TT10 = pd.DataFrame(TT10scaled, columns = TT10c)

TT10 = pd.concat([TT10_idx, TT10], axis = 1)
TT10 = TT10.set_index('index')

In [137]:
from pycaret.regression import *
TT05_prediction = predict_model(T05_final_regression_model, data=TT05)
TT01_prediction = predict_model(T01_final_regression_model, data=TT01)
TT10_prediction = predict_model(T10_final_regression_model, data=TT10)

TT05_prediction = pd.DataFrame(TT05_prediction, columns = ['prediction_label'])
TT01_prediction = pd.DataFrame(TT01_prediction, columns = ['prediction_label'])
TT10_prediction = pd.DataFrame(TT10_prediction, columns = ['prediction_label'])

In [138]:
TT05_y_class = pd.DataFrame(TT05, columns = ['PRODUCT_CODE'])
TT05_idx = TT05_y_class.index
TT05_y_class = TT05_y_class.reset_index()
TT05_prediction = pd.concat([TT05_prediction, TT05_y_class], axis = 1)
TT05_prediction = TT05_prediction.set_index('index')
TT05_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

TT01_y_class = pd.DataFrame(TT01, columns = ['PRODUCT_CODE'])
TT01_idx = TT01_y_class.index
TT01_y_class = TT01_y_class.reset_index()
TT01_prediction = pd.concat([TT01_prediction, TT01_y_class], axis = 1)
TT01_prediction = TT01_prediction.set_index('index')
TT01_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

TT10_y_class = pd.DataFrame(TT10, columns = ['PRODUCT_CODE'])
TT10_idx = TT10_y_class.index
TT10_y_class = TT10_y_class.reset_index()
TT10_prediction = pd.concat([TT10_prediction, TT10_y_class], axis = 1)
TT10_prediction = TT10_prediction.set_index('index')
TT10_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [139]:
TT05_datas = TT05_prediction['prediction_label']
TT05_datas = pd.DataFrame(TT05_datas.values, columns = ['Y_Quality'])

TT05y_idx= TT05_prediction.index
TT05y_idx = pd.DataFrame(TT05y_idx, columns = ['index'])
TT05_datas = pd.concat([TT05y_idx, TT05_datas], axis = 1)
TT05_datas = TT05_datas.set_index('index')

TT01_datas = TT01_prediction['prediction_label']
TT01_datas = pd.DataFrame(TT01_datas.values, columns = ['Y_Quality'])

TT01y_idx= TT01_prediction.index
TT01y_idx = pd.DataFrame(TT01y_idx, columns = ['index'])
TT01_datas = pd.concat([TT01y_idx, TT01_datas], axis = 1)
TT01_datas = TT01_datas.set_index('index')

TT10_datas = TT10_prediction['prediction_label']
TT10_datas = pd.DataFrame(TT10_datas.values, columns = ['Y_Quality'])

TT10y_idx= TT10_prediction.index
TT10y_idx = pd.DataFrame(TT10y_idx, columns = ['index'])
TT10_datas = pd.concat([TT10y_idx, TT10_datas], axis = 1)
TT10_datas = TT10_datas.set_index('index')

In [140]:
from pycaret.classification import *

TT05_predictions = predict_model(T05_final_classification_model, data=TT05_datas)
TT01_predictions = predict_model(T01_final_classification_model, data=TT01_datas)
TT10_predictions = predict_model(T10_final_classification_model, data=TT10_datas)

TT05_predictions = pd.DataFrame(TT05_predictions, columns = ['prediction_label'])
TT01_predictions = pd.DataFrame(TT01_predictions, columns = ['prediction_label'])
TT10_predictions = pd.DataFrame(TT10_predictions, columns = ['prediction_label'])

In [141]:
TT05_idxf = TT05_datas.index
TT05_p = pd.DataFrame(TT05_idxf, columns = ['index'])
TT05_predictions = pd.concat([TT05_p, TT05_predictions], axis = 1)
TT05_predictions = TT05_predictions.set_index('index')

TT01_idxf = TT01_datas.index
TT01_p = pd.DataFrame(TT01_idxf, columns = ['index'])
TT01_predictions = pd.concat([TT01_p, TT01_predictions], axis = 1)
TT01_predictions = TT01_predictions.set_index('index')

TT10_idxf = TT10_datas.index
TT10_p = pd.DataFrame(TT10_idxf, columns = ['index'])
TT10_predictions = pd.concat([TT10_p, TT10_predictions], axis = 1)
TT10_predictions = TT10_predictions.set_index('index')

In [142]:
final_test = pd.concat([TT05_predictions, TT01_predictions, TT10_predictions])
final_test

prediction_label
index                  
3                     0
4                     1
5                     1
6                     2
7                     0
...                 ...
309                   1
138                   1
256                   1
257                   1
287                   1

[310 rows x 1 columns]

In [143]:
final_test = final_test.sort_index(ascending=True)
final_test['prediction_label']

index
0      1
1      1
2      1
3      0
4      1
      ..
305    1
306    1
307    1
308    1
309    1
Name: prediction_label, Length: 310, dtype: int32

In [147]:
#52
sample_submission = pd.read_csv('sample_submission.csv')
sample_submission['Y_Class'] = final_test['prediction_label']
display(sample_submission.head())
sample_submission.to_csv('pcode_dropotherstd0_75up_robust_regpyc_classpyc_fillmean_submission.csv',index=False)

PRODUCT_ID  Y_Class
0   TEST_000        1
1   TEST_001        1
2   TEST_002        1
3   TEST_003        0
4   TEST_004        1

In [145]:
np.array(final_test['prediction_label'])

array([1, 1, 1, 0, 1, 1, 2, 0, 0, 1, 1, 1, 2, 1, 0, 0, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 2, 0, 1, 0, 0, 1,
       1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 1, 0, 1, 1, 0, 0, 0, 0, 1, 1, 0, 0,
       0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 0, 1,
       0, 0, 2, 1, 2, 2, 1, 2, 1, 1, 1, 2, 1, 2, 1, 2, 1, 1, 2, 1, 2, 1,
       1, 1, 1, 2, 1, 1, 1, 0, 1, 2, 1, 1, 2, 2, 1, 1, 2, 1, 1, 1, 1, 1,
       1, 1, 2, 2, 1, 2, 1, 1, 1, 1, 0, 1, 2, 1, 1, 2, 1, 1, 1, 2, 1, 1,
       1, 1, 1, 1, 1, 1, 2, 2, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 2, 1, 1, 1,
       2, 1, 1, 2, 1, 1, 1, 2, 1, 1, 1, 2, 1, 2, 1, 2, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 2,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,

In [146]:
final_test['prediction_label'].value_counts()

1    241
2     40
0     29
Name: prediction_label, dtype: int64